In [4]:
import requests
from bs4 import BeautifulSoup
from pymongo import MongoClient
import random

import os

import dotenv

In [1]:
user_agents = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/60.0.3112.78 Safari/537.36 OPR/47.0.2631.39",
    "Mozilla/5.0 (Windows NT 6.1; WOW64; Trident/7.0; AS; rv:11.0) like Gecko",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_12_5) AppleWebKit/603.2.4 (KHTML, like Gecko) Version/10.1.1 Safari/603.2.4",
    "My User Agent 1.0",
]

In [2]:
sjsu_page = "https://www.sjsu.edu/"

In [5]:
def scrape_links_from_page():
    print("Scraping Page...")
    url = "https://www.sjsu.edu/"
    headers = {"User-Agent": random.choice(user_agents)}
    response = requests.get(url, headers=headers)
    soup = BeautifulSoup(response.content, "html.parser")
    links = [a.get('href') for a in soup.find_all('a', href=True)]
    # return links
    print(len(links))
    # for link in links:
    #     print(link)
    return links
all_links= scrape_links_from_page()

Scraping Page...
161


In [6]:
def separate_links(links):
    http_links = [link for link in links if link.startswith('http')]
    non_http_links = [link for link in links if not link.startswith('http')]
    return http_links, non_http_links

http_links, non_http_links = separate_links(all_links)
print("HTTP Links: ", len(http_links))
print("Non-HTTP Links: ", len(non_http_links))

print("HTTP Links: ", non_http_links)


HTTP Links:  146
Non-HTTP Links:  15
HTTP Links:  ['#maincontent', '/', '/visit/index.php', '/admissions/index.php', '/giving/', '/online/index.php?utm_source=sjsumainmenu&utm_medium=web&utm_campaign=sjsuonline-navmenu-traffic', '/giving/', '/index.php', '/online/index.php?utm_source=sjsumainmenu-mobile&utm_medium=web&utm_campaign=sjsuonline-navmenu-traffic', '/about/', '', '/facts-and-accomplishments/', '/online/', 'tel:4089241000', '/online/index.php']


In [7]:
def add_prefix_to_links(links, prefix):
    return [prefix + link for link in links]

final_non_http_links = add_prefix_to_links(non_http_links, sjsu_page)

# print("Final Non-HTTP Links: ", final_non_http_links)


final_links = final_non_http_links + http_links
final_links = [link.replace("https://one.sjsu.edu", "").strip() for link in final_links]
final_links = [link for link in final_links if link]
# Save links to a text file
with open("final_links.txt", "w") as f:
    for link in final_links:
        f.write(link + "\n")

print("Final Links: ", len(final_links))

Final Links:  160


In [8]:
print("Final Links: ", final_links[59])

Final Links:  http://www.sjsu.edu/search/index.html


In [18]:
from langchain_community.document_loaders import WebBaseLoader
import bs4
import json

dataList = []

def scrapePages(urls):    
    urls = [url for url in urls if url]
    print("URLs are: ", urls)
    loader = WebBaseLoader(
        web_paths=urls,
        ###Specify the classname for dynamic webpages
        bs_kwargs=dict(
            # parse_only=bs4.SoupStrainer(class_=("group", "ArticleHeader-headline"))
        ),
    )
    print(loader)
 
    data = loader.load()
    dataList.append(data)
    print("Data object length is: ", len(data))


urls = final_links
scrapePages(urls)

# print("Data List: ", dataList[0])
# Convert Document objects to a serializable format
serializable_data = []
for doc in dataList:
    for document in doc:  # Assuming doc is a list of Document objects
        serializable_data.append(
            {
                "metadata": document.metadata,  # Extract metadata
                "page_content": document.page_content,  # Extract page content
            }
        )

# Save the entire serializable_data as a JSON file after the function call
with open("scraped_data.json", "w", encoding="utf-8") as json_file:
    json.dump(
        serializable_data, json_file, ensure_ascii=False, indent=4
    )  # Save with pretty formatting

print("Data List: ", serializable_data)

URLs are:  ['https://www.sjsu.edu/#maincontent', 'https://www.sjsu.edu//', 'https://www.sjsu.edu//visit/index.php', 'https://www.sjsu.edu//admissions/index.php', 'https://www.sjsu.edu//giving/', 'https://www.sjsu.edu//online/index.php?utm_source=sjsumainmenu&utm_medium=web&utm_campaign=sjsuonline-navmenu-traffic', 'https://www.sjsu.edu//giving/', 'https://www.sjsu.edu//index.php', 'https://www.sjsu.edu//online/index.php?utm_source=sjsumainmenu-mobile&utm_medium=web&utm_campaign=sjsuonline-navmenu-traffic', 'https://www.sjsu.edu//about/', 'https://www.sjsu.edu/', 'https://www.sjsu.edu//facts-and-accomplishments/', 'https://www.sjsu.edu//online/', 'https://www.sjsu.edu/tel:4089241000', 'https://www.sjsu.edu//online/index.php', 'https://www.sjsu.edu/visit/index.php', 'https://www.sjsu.edu/soar/services/campus-tours.php', 'http://www.sjsu.edu/map', 'https://www.sjsu.edu/parking/', 'https://www.sjsu.edu/visit/silicon-valley.php', 'https://hammertheatre.com/', 'https://www.sjsu.edu/sjsuloves

In [53]:
def clean_empty_lines(input_file, output_file):
    with open(input_file, "r", encoding="utf-8") as infile:
        lines = infile.readlines()

    # Remove empty lines and strip whitespace
    cleaned_lines = [line.strip() for line in lines if line.strip()]

    with open(output_file, "w", encoding="utf-8") as outfile:
        for line in cleaned_lines:
            outfile.write(line + "\n")


clean_empty_lines("scraped_pages_content.txt", "filtered_data.txt")

In [57]:
import re

# Load the text data
with open("scraped_pages_content.txt", "r", encoding="utf-8") as file:
    text = file.read()

# Step 1: Remove boilerplate content by identifying common navigational patterns
patterns = [
    r"Skip to main content",
    r"Search",
    r"Visit",
    r"Apply",
    r"Give",  # Common phrases
    r"SJSU on [A-Za-z]+",
    r"SJSU Online",  # Social media links
    r"Footer",
    r"Last Updated .*",  # Footer and Last updated information
]
for pattern in patterns:
    text = re.sub(pattern, "", text)

# Step 2: Remove excessive whitespace
text = re.sub(r"\n\s*\n", "\n", text)  # Reduce multiple newlines to a single newline

# Step 3: Remove repetitive sections
# Example: We could split sections by keywords and check for duplicates
unique_sections = list(set(text.split("\n\n")))  # Split and deduplicate sections
cleaned_text = "\n\n".join(unique_sections)

# Step 4: Save the cleaned text
with open("cleaned_scraped_contentL1.txt", "w", encoding="utf-8") as file:
    file.write(cleaned_text)

In [58]:
import re


def clean_noisy_data(text):
    # Define a regex pattern to match unwanted characters
    # This pattern removes non-printable characters and any other specified noise
    cleaned_text = re.sub(
        r"[^\x20-\x7E]+", "", text
    )  # Keep only printable ASCII characters
    return cleaned_text


def clean_file(input_file, output_file):
    with open(input_file, "r", encoding="utf-8", errors="ignore") as infile:
        lines = infile.readlines()

    cleaned_lines = [clean_noisy_data(line) for line in lines]

    with open(output_file, "w", encoding="utf-8") as outfile:
        for line in cleaned_lines:
            if line.strip():  # Only write non-empty lines
                outfile.write(line + "\n")


# Usage
clean_file("cleaned_scraped_contentL1.txt", "cleaned_scraped_contentL2.txt")